In [11]:
import pandas as pd
import numpy as np
import datetime as date
import matplotlib.pyplot as plt
import queue 
import math
import time
today=date.date.today()
print(today)
import pyodbc
#from pyxlsb import open_workbook
connection = pyodbc.connect(
    driver='{iSeries Access ODBC Driver}',
    system='KNL400A',
    #uid='JSKEATH',
    #pwd='DUSTY35')
    uid = 'TSCHMITT',
    pwd = '$HSV123')
    

pd.options.display.max_rows = 50000
cursor = connection.cursor()

2021-09-13


In [12]:
#relevant fridays 
faketoday = date.datetime.now() + date.timedelta(hours = 132)
faketoday = faketoday.date()

friday0 = faketoday + date.timedelta(days = 4 - faketoday.weekday())           #this friday
friday_1 = faketoday + date.timedelta(days = -3 - faketoday.weekday())         #last friday
friday1 = faketoday + date.timedelta(days = 11 - faketoday.weekday())          #next friday
friday2 = faketoday + date.timedelta(days = 18 - faketoday.weekday())          #friday 2 weeks from now 
friday3 = faketoday + date.timedelta(days = 25 - faketoday.weekday())          #friday 3 weeks from now  
friday4 = faketoday + date.timedelta(days = 32 - faketoday.weekday())          #friday 4 weeks from now 

print(faketoday)
print("friday0:",friday0,"friday_1:",friday_1,"friday1:",friday1,"friday2:",friday2,"friday3:",friday3,"friday4:",friday4)
print("Update initiated. Total wait time ~10 min")

2021-09-19
friday0: 2021-09-17 friday_1: 2021-09-10 friday1: 2021-09-24 friday2: 2021-10-01 friday3: 2021-10-08 friday4: 2021-10-15
Update initiated. Total wait time ~10 min


In [13]:
data = [['Current Week:', friday0], ['Next Week:', friday1], ['Two Weeks Out:', friday2]]
whatweeks = pd.DataFrame(data, columns = ['Week', 'Date'])
#whatweeks.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\whatweekisit.xlsx')
#whatweeks.to_excel(r'T:\share\Thomas\whatweekisit.xlsx')

In [14]:
timer1 = time.perf_counter()
#import TinaPaint file, rename columns
lookup = pd.read_sql_query('select * from KNL400A.EGLIB.TINAPAINTX',connection)
lookup = lookup.rename(columns={"IBPRP4":"MPF","WADRQJ":"PDATE","WARCTO":"SO TYPE","WALITM":"PATTERN NUMBER","IMDSC1":"PATTERN DESCRIPTION","OPENQTY":"OPEN PATTERN QTY","WAUOM":"UOM","WARORN":"SALES ORDER","WADCTO":"SALES TYPE","WADOCO":"WORK ORDER","WALNID":"SALES LINE","WAUORG":"INITIAL WA QTY","WASRST":"WORK ORDER STATUS","WAWR01":"COLOR","WAWR07":"MIXING CENTER","WMCPIL":"COMPONENTS","WMUORG":"COMPONENT QTY","WAANSA01":"MANAGER NAME","IBANPL01":"PLANNER NAME","IBBUYR01":"BUYER NAME","IBCOTY":"COMPLETED QTY","IBSTKT01":"PATTERN TYPE","IBPRP401":"MPF DESCRIPTION","WMCPNT":"COMP TYPE","WMUKID":"UNIQUE ID","WMCPIA":"3RD COMP"})
lookup = lookup[['MPF','PDATE','SO TYPE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SALES ORDER','WORK ORDER','SALES LINE','INITIAL WA QTY','WORK ORDER STATUS','COLOR','COMPONENTS','COMPONENT QTY','MANAGER NAME','PATTERN TYPE','MPF DESCRIPTION']]

#date manipulation of tinapaint date to friday, removal of 10/10/50s
lookup = lookup[lookup.PDATE != '10/10/50']
lookup.reset_index(drop=True,inplace=True)
lookup.loc[:,'WORK ORDER STATUS'] = (lookup['WORK ORDER STATUS']).astype('int32')
lookup.loc[:,'WORK ORDER'] = (lookup['WORK ORDER']).astype('int32')
lookup['PDATE'] = lookup['PDATE'].apply(lambda x: date.datetime.strptime(x,"%m/%d/%y"))
lookup['PDATE'] = lookup['PDATE'].apply(lambda x: x + date.timedelta(days = 4 - x.weekday()))
lookup['PDATE'] = lookup['PDATE'].apply(lambda x: x.date())
lookup['COMPONENTS']=lookup['COMPONENTS'].apply(lambda x: str(x))
lookup['COMPONENTS']=lookup['COMPONENTS'].apply(lambda x: x.strip())
lookup.loc[:,'COMPONENT QTY'] = (lookup['COMPONENT QTY']).astype('int32')

#truncation of data to smaller timeframe
monthago = friday0 - date.timedelta(30)
lookup = lookup[lookup.PDATE <= friday3]
lookup = lookup[lookup.PDATE > monthago]

#get rid of duplicate rows in tinapaint
lookup.drop_duplicates(subset=['WORK ORDER', 'COMPONENTS','COMPONENT QTY'],inplace=True)
lookup.reset_index(drop=True,inplace=True)

#import and merge MPF key to dataframe to add areas
mpfkey = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\MPFareas.xlsx', usecols = "A,B")
##mpfkey = pd.read_excel('T:\share\Thomas\MPFareas.xlsx', usecols = "A,B")
lookup['MPF'] = lookup['MPF'].astype(str)
lookup = pd.merge(lookup,mpfkey,how = "left",on = "MPF")
lookup.COLOR.replace('    ',"N/A",inplace = True)
lookup['COLOR'] = lookup['COLOR'].apply(lambda x: x.strip())

#import and merge routing assembly times to dataframe; unique to each WA 
routingkey = pd.read_sql_query('select * from KNL400A.JDEQUERY.SEATMONJDX',connection)
routingkey = routingkey[['SDPPDJ','SDRORN','SDLITM','SDDSC1','SDUORG','WLRUNL','WLDSC1','WLMCU']]
routingkey['SDRORN'] = routingkey['SDRORN'].apply(lambda x: x.strip())
routingkey['SDLITM'] = routingkey['SDLITM'].apply(lambda x: x.strip())
routingkey['WLMCU'] = routingkey['WLMCU'].apply(lambda x: x.strip())
routingkey = routingkey[~routingkey.WLMCU.isin(['E62347','GAP000','E62338','E80125','E81144','E81149','E80138','E81162','E81177','E81903','E81148','E81153'])]
routingkey = routingkey.groupby(['SDPPDJ','SDRORN','SDLITM','WLMCU'],as_index=False).agg({'WLRUNL': 'sum'})
routingkey = routingkey.groupby(['SDPPDJ','SDRORN','SDLITM'],as_index=False).agg({'WLRUNL': 'sum'})
routingkey['SDPPDJ'] = routingkey['SDPPDJ'].apply(lambda x: date.datetime.strptime(x,"%m/%d/%y"))
routingkey['SDPPDJ'] = routingkey['SDPPDJ'].apply(lambda x: x.date())
routingkey = routingkey.sort_values(by=['SDPPDJ'])
routingkey = routingkey.rename(columns={"SDPPDJ":"DATE","SDRORN":"WORK ORDER","SDLITM":"PATTERN NUMBER","SDDSC1":"PATTERN DESCRIPTION","SDUORG":"INITIAL WA QTY","WLRUNL":"Hours Work","WLDSC1":"ACTION DESCRIPTION","WLMCU":"WORKING CENTER"})
routingkey.reset_index(drop=True,inplace=True)
routingkey['PATTERN NUMBER'] = routingkey['PATTERN NUMBER'].apply(lambda x: str(x))
routingkey['WORK ORDER'] = routingkey['WORK ORDER'].apply(lambda x: str(int(x)))
lookup['PATTERN NUMBER'] = lookup['PATTERN NUMBER'].apply(lambda x: x.strip())
lookup['WORK ORDER'] = lookup['WORK ORDER'].apply(lambda x: str(int(x)))
lookup = lookup.sort_values(by=['WORK ORDER'])
lookup=pd.merge(lookup,routingkey, how="left",on=['WORK ORDER','PATTERN NUMBER'])

#for WAs not shown in routingkey, take converted tinapaint date and manually compute routings using area averages
lookup['DATE'].fillna(lookup['PDATE'], inplace=True)
lookup.drop(columns=['PDATE'],inplace=True)

hoursalert = lookup[lookup['Hours Work'].isna()]
#hoursalert.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\hoursalert.xlsx')
#hoursalert.to_excel(r'T:\share\Thomas\hoursalert.xlsx')

gl = lookup[lookup['AREA'] == 'Glass']
lg = lookup[lookup['AREA'] == 'Legs']
pp = lookup[lookup['AREA'] == 'Paint/Pack']
ro = lookup[lookup['AREA'] == 'Rockwell']
s5 = lookup[lookup['AREA'] == 'Station 50']
sy = lookup[lookup['AREA'] == 'Sys Assy']
ta = lookup[lookup['AREA'] == 'Tables']
gl['delete1'] = gl['INITIAL WA QTY']* 0.035
gl = gl[['WORK ORDER','delete1']]
lg['delete1'] = lg['INITIAL WA QTY']* 0.02
lg = lg[['WORK ORDER','delete1']]
pp['delete1'] = pp['INITIAL WA QTY']* 0.004
pp = pp[['WORK ORDER','delete1']]
ro['delete1'] = ro['INITIAL WA QTY']* 0.025
ro = ro[['WORK ORDER','delete1']]
s5['delete1'] = s5['INITIAL WA QTY']* 0.014
s5 = s5[['WORK ORDER','delete1']]
sy['delete1'] = sy['INITIAL WA QTY']* 0.054
sy = sy[['WORK ORDER','delete1']]
ta['delete1'] = ta['INITIAL WA QTY']* 0.04
ta = ta[['WORK ORDER','delete1']]

gl.drop_duplicates(inplace=True)
lg.drop_duplicates(inplace=True)
pp.drop_duplicates(inplace=True)
ro.drop_duplicates(inplace=True)
s5.drop_duplicates(inplace=True)
sy.drop_duplicates(inplace=True)
ta.drop_duplicates(inplace=True)

lookup = pd.merge(lookup,gl, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,lg, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,pp, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,ro, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,s5, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,sy, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,ta, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)

#import and merge Vendor key to dataframe 
vendkey=pd.read_sql_query('select * from KNL400A.JDEQUERY.JDSBOMSXX',connection)
vendkey = vendkey[['IBVEND','IBVEND01','WMCPIL']]
vendkey = vendkey.drop_duplicates()
vendkey = vendkey.sort_values(by=['IBVEND'])
vendkey = vendkey.drop_duplicates(subset='WMCPIL', keep="last")
vendkey = vendkey[['IBVEND01','WMCPIL']]
vendkey=vendkey.rename(columns={"IBVEND01":"Supplier","WMCPIL":"COMPONENTS"})
vendkey['COMPONENTS']=vendkey['COMPONENTS'].apply(lambda x: x.strip())
vendkey.reset_index(drop=True,inplace=True)

lookup=pd.merge(lookup,vendkey,how="left",on="COMPONENTS")
lookup['Supplier']=lookup['Supplier'].fillna('ERROR')
lookup.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)

#change sales color codes to in house color codes
lookup.COLOR.replace('111','E40',inplace=True)
lookup.COLOR.replace('112','EB8',inplace=True)
lookup.COLOR.replace('113','EDS',inplace=True)
lookup.COLOR.replace('114','EFS',inplace=True)
lookup.COLOR.replace('115','EL9',inplace=True)
lookup.COLOR.replace('116','EHS',inplace=True)
lookup.COLOR.replace('117','EJ9',inplace=True)
lookup.COLOR.replace('118','EKS',inplace=True)
lookup.COLOR.replace('119','EUS',inplace=True)
lookup.COLOR.replace('120S','120',inplace=True)
lookup.COLOR.replace('611','EMS',inplace=True)
lookup.COLOR.replace('612','EG2',inplace=True)
lookup.COLOR.replace('613','ERS',inplace=True)
lookup.COLOR.replace('130','E0S',inplace=True)
lookup.COLOR.replace('131','E1S',inplace=True)
lookup.COLOR.replace('111S','E40',inplace=True)
lookup.COLOR.replace('112S','EB8',inplace=True)
lookup.COLOR.replace('113S','EDS',inplace=True)
lookup.COLOR.replace('114S','EFS',inplace=True)
lookup.COLOR.replace('115S','EL9',inplace=True)
lookup.COLOR.replace('116S','EHS',inplace=True)
lookup.COLOR.replace('117S','EJ9',inplace=True)
lookup.COLOR.replace('118S','EKS',inplace=True)
lookup.COLOR.replace('119S','EUS',inplace=True)
lookup.COLOR.replace('611S','EMS',inplace=True)
lookup.COLOR.replace('612S','EG2',inplace=True)
lookup.COLOR.replace('613S','ERS',inplace=True)
lookup.COLOR.replace('130S','E0S',inplace=True)
lookup.COLOR.replace('131S','E1S',inplace=True)
lookup.COLOR.replace('111T','ET2',inplace=True)
lookup.COLOR.replace('112T','EB7',inplace=True)
lookup.COLOR.replace('113T','EDT',inplace=True)
lookup.COLOR.replace('114T','EFT',inplace=True)
lookup.COLOR.replace('115T','EZ5',inplace=True)
lookup.COLOR.replace('116T','EHT',inplace=True)
lookup.COLOR.replace('117T','EJ0',inplace=True)
lookup.COLOR.replace('118T','EKT',inplace=True)
lookup.COLOR.replace('119T','EUT',inplace=True)
lookup.COLOR.replace('611T','EMT',inplace=True)
lookup.COLOR.replace('612T','EK2',inplace=True)
lookup.COLOR.replace('613T','EK5',inplace=True)
lookup.COLOR.replace('130T','E0T',inplace=True)
lookup.COLOR.replace('131T','E1T',inplace=True)

lookup = lookup[['MPF','DATE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SO TYPE','SALES ORDER','WORK ORDER','SALES LINE','INITIAL WA QTY','WORK ORDER STATUS','COLOR','COMPONENTS','COMPONENT QTY','MANAGER NAME','PATTERN TYPE','MPF DESCRIPTION','AREA','Hours Work','Supplier']]


vendoralert = lookup[lookup['Supplier'] == 'ERROR']
#vendoralert.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\vendoralert.xlsx')
#vendoralert.to_excel(r'T:\share\Thomas\vendoralert.xlsx')

timer2 = time.perf_counter()
print('load time:')
print(timer2 - timer1)

<ipython-input-14-6a43ab133ada>:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gl['delete1'] = gl['INITIAL WA QTY']* 0.035
<ipython-input-14-6a43ab133ada>:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  lg['delete1'] = lg['INITIAL WA QTY']* 0.02
<ipython-input-14-6a43ab133ada>:76: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/

load time:
221.95213769999998


In [145]:
#add assembly staffing factors; must be >0 
#staffkey = pd.read_excel('T:\share\Thomas\AssemblyStaffing.xlsx', usecols = "A,B")
#lookup=pd.merge(lookup,staffkey,how="left",on="AREA")
#lookup['Hours Work'] = lookup['Hours Work'] / lookup['Staff Factor']


In [16]:
allcomps1 = lookup[lookup.DATE <= friday0 - date.timedelta(days = 2)]
allcomps2 = lookup[lookup.DATE <= friday0]
allcomps3 = lookup[lookup.DATE <= friday1 - date.timedelta(days = 2)]
allcomps4 = lookup[lookup.DATE <= friday1]
allcomps5 = lookup[lookup.DATE <= friday2 - date.timedelta(days = 2)]
allcomps6 = lookup[lookup.DATE <= friday2]

lookupforweek1 = allcomps1.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek1 = lookupforweek1.sort_values(by=['Hours Work'])
lookupforweek1.reset_index(drop=True,inplace=True)

lookupforweek2 = allcomps2.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek2 = lookupforweek2.sort_values(by=['Hours Work'])
lookupforweek2.reset_index(drop=True,inplace=True)

lookupforweek3 = allcomps3.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek3 = lookupforweek3.sort_values(by=['Hours Work'])
lookupforweek3.reset_index(drop=True,inplace=True)

lookupforweek4 = allcomps4.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek4 = lookupforweek4.sort_values(by=['Hours Work'])
lookupforweek4.reset_index(drop=True,inplace=True)

lookupforweek5 = allcomps5.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek5 = lookupforweek5.sort_values(by=['Hours Work'])
lookupforweek5.reset_index(drop=True,inplace=True)

lookupforweek6 = allcomps6.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek6 = lookupforweek6.sort_values(by=['Hours Work'])
lookupforweek6.reset_index(drop=True,inplace=True)


In [19]:
#week selection: lookupforweek = lookupclean .... that has date; PAST DUE BEING ADDED UP TO 1 MONTH BACK for current week
#allcomps: all orders, components, etc. for the week; 3 week view 
allcomps7 = lookup[lookup.DATE <= friday0]
allcomps7 = allcomps7[allcomps7.DATE > monthago]
allcomps14 = lookup[lookup.DATE == friday1]
allcomps21 = lookup[lookup.DATE == friday2]

#lookupforweeks: orders grouped by WA on the pattern level; 3 week view
lookupforweek7 = allcomps7.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek7 = lookupforweek7.sort_values(by=['Hours Work'])
lookupforweek7.reset_index(drop=True,inplace=True)

lookupforweek14 = allcomps14.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek14 = lookupforweek14.sort_values(by=['Hours Work'])
lookupforweek14.reset_index(drop=True,inplace=True)

lookupforweek21 = allcomps21.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek21 = lookupforweek21.sort_values(by=['Hours Work'])
lookupforweek21.reset_index(drop=True,inplace=True)

#status40s: orders grouped by WA, only status >=40 with hours aggregated 
status40_7 = lookupforweek7[lookupforweek7['WORK ORDER STATUS'] > 39] 
status40_7 = status40_7.sort_values(by=['Hours Work'])
status40_7.reset_index(drop=True,inplace=True)

status40_14 = lookupforweek14[lookupforweek14['WORK ORDER STATUS'] > 39] 
status40_14 = status40_14.sort_values(by=['Hours Work'])
status40_14.reset_index(drop=True,inplace=True)

status40_21 = lookupforweek21[lookupforweek21['WORK ORDER STATUS'] > 39] 
status40_21 = status40_21.sort_values(by=['Hours Work'])
status40_21.reset_index(drop=True,inplace=True)

In [17]:
#Hours of work per assembly area per color 
def mpf_assy(weeklookup):

    lookupmpf=weeklookup.pivot_table(values='Hours Work',index=['AREA'],columns='COLOR',aggfunc=np.sum)
    lookupmpf=lookupmpf.fillna(0)
    lookupmpf.mask((lookupmpf > 0) & (lookupmpf < 0.001), 0.001, inplace=True)
    pd.options.display.max_columns = 50
    #lookupmpf[lookupmpf.index == 'Glass'] = lookupmpf[lookupmpf.index == 'Glass'].div(glass_coeff)
    lookupmpf.loc['Color Totals']= lookupmpf.sum(numeric_only=True, axis=0)
    lookupmpf.loc[:,'Area Totals'] = lookupmpf.sum(numeric_only=True, axis=1)

    return lookupmpf

#lookupmpf.head(100)

In [18]:
#lookupmpf, but flipped along the diagonal 
def col_assy(weeklookup):

    lookupcol=weeklookup.pivot_table(values='Hours Work',index=['COLOR'],columns='AREA',aggfunc=np.sum)
    lookupcol=lookupcol.fillna(0)
    lookupcol.mask((lookupcol > 0) & (lookupcol < 0.001), 0.001, inplace=True)
    #lookupcol['Glass'] = lookupcol['Glass'].div(glass_coeff)
    lookupcol.loc['Area Totals']= lookupcol.sum(numeric_only=True, axis=0)
    lookupcol.loc[:,'Color Totals'] = lookupcol.sum(numeric_only=True, axis=1)

    return lookupcol

#pd.options.display.max_columns = 50
#lookupcol.head(100)

In [19]:
mpf1 = mpf_assy(lookupforweek1)
mpf2 = mpf_assy(lookupforweek2)
mpf3 = mpf_assy(lookupforweek3)
mpf4 = mpf_assy(lookupforweek4)
mpf5 = mpf_assy(lookupforweek5)
mpf6 = mpf_assy(lookupforweek6)

In [24]:
col1 = col_assy(lookupforweek1)
col2 = col_assy(lookupforweek2)
col3 = col_assy(lookupforweek3)
col4 = col_assy(lookupforweek4)
col5 = col_assy(lookupforweek5)
col6 = col_assy(lookupforweek6)

In [22]:
mpf7 = mpf_assy(lookupforweek7)
col7 = col_assy(lookupforweek7)
mpf14 = mpf_assy(lookupforweek14)
col14 = col_assy(lookupforweek14)
mpf21 = mpf_assy(lookupforweek21)
col21 = col_assy(lookupforweek21)

In [25]:
#find area with most work, find all colors with work in that area, then choose the color with largest total hours, repeat
def paint_schedule(lookupmpf,lookupcol):
    colors = []
    colcopy = lookupcol.drop('Area Totals')
    colcopy = colcopy.drop('Color Totals', axis=1)
    mpfcopy = lookupmpf.drop('Color Totals')
    mpfcopy = mpfcopy.drop('Area Totals', axis=1)
    colcopy = round(colcopy,3)
    mpfcopy = round(mpfcopy,3)
    
    n = range(len(lookupmpf.columns.tolist()) - 1)
    
    for i in n: 
        
        colcopy.loc['Area Totals']= colcopy.sum(numeric_only=True, axis=0)
        colcopy.loc[:,'Color Totals'] = colcopy.sum(numeric_only=True, axis=1)
        mpfcopy.loc['Color Totals']= mpfcopy.sum(numeric_only=True, axis=0)
        mpfcopy.loc[:,'Area Totals'] = mpfcopy.sum(numeric_only=True, axis=1)
        #print(colcopy)
        colcopy = round(colcopy,3)
        mpfcopy = round(mpfcopy,3)   
    
        colnum = len(colcopy.columns)
        vals = colcopy.iloc[-1][0:colnum-1].values
        maxval = round(max(vals),3)
        
        temp = mpfcopy.loc[mpfcopy['Area Totals'] == maxval]
        #print(maxval)

        temp1 = colcopy[temp.index[0]] 
        
        #print(temp1)

        temp1 = temp1[temp1.values == 0] 

        #print(temp1.index.values)
        colortotals = colcopy['Color Totals']
        
        #print(colortotals)
        colortotals = colortotals.drop(temp1.index.values)
        colortotals = colortotals.drop('Area Totals')
        #print(colortotals)
        colortotals = colortotals[colortotals.values == max(colortotals)]
        colors.append(str(colortotals.index.values[0]))

        #print(colors)

        colcopy = colcopy.drop(colortotals.index.values[0])
        colcopy = colcopy.drop('Area Totals')
        colcopy = colcopy.drop('Color Totals', axis=1)
        mpfcopy = mpfcopy.drop(colortotals.index.values[0], axis=1)
        mpfcopy = mpfcopy.drop('Color Totals')
        mpfcopy = mpfcopy.drop('Area Totals', axis=1)

        #print(mpfcopy)
    
    return colors

In [26]:
paint1 = paint_schedule(mpf1, col1)
paint2 = paint_schedule(mpf2, col2)
paint3 = paint_schedule(mpf3, col3)
paint4 = paint_schedule(mpf4, col4)
paint5 = paint_schedule(mpf5, col5)
paint6 = paint_schedule(mpf6, col6)

In [ ]:
paint7 = paint_schedule(mpf7, col7)
paint14 = paint_schedule(mpf14, col14)
paint21 = paint_schedule(mpf21, col21)

In [27]:
#filter out all components from the metal shop for MS scheduling
def create_lookupms(lookupforweek, paintlist):
    
    lookupforweekms = pd.DataFrame()
    
    for i in range(len(paintlist)):

        appendthis = lookupforweek[lookupforweek['COLOR'] == paintlist[i]]
        lookupforweekms = lookupforweekms.append(appendthis)
        lookupforweekms.reset_index(drop=True,inplace=True)

    lookupforweekms = lookupforweekms[lookupforweekms.Supplier == 'METAL SHOP']
    lookupforweekms.reset_index(drop=True,inplace=True)
    return lookupforweekms

In [28]:
lookupforweekms1 = create_lookupms(allcomps1, paint1)
lookupforweekms2 = create_lookupms(allcomps2, paint2)
lookupforweekms3 = create_lookupms(allcomps3, paint3)
lookupforweekms4 = create_lookupms(allcomps4, paint4)
lookupforweekms5 = create_lookupms(allcomps5, paint5)
lookupforweekms6 = create_lookupms(allcomps6, paint6)

In [26]:
lookupforweekms7 = create_lookupms(allcomps7, paint7)
lookupforweekms14 = create_lookupms(allcomps14, paint14)
lookupforweekms21 = create_lookupms(allcomps21, paint21)

In [29]:
routingkey1 = pd.read_sql_query('select * from KNL400A.JDEQUERY.ROUTSDLB',connection)
routingkey1 = routingkey1[['IRKITL','IRDSC1','IRRUNL']]
routingkey1['IRKITL'] = routingkey1['IRKITL'].apply(lambda x: x.strip())
routingkey1['IRRUNL'] = routingkey1['IRRUNL'].apply(lambda x: x/100)
routingkey1 = routingkey1.drop_duplicates(subset=['IRKITL','IRDSC1'])
routingkey1 = routingkey1.groupby(['IRKITL'],as_index=False).agg({'IRRUNL': 'sum'})
routingkey1 = routingkey1.rename(columns={"IRKITL":"COMPONENTS","IRDSC1":"ACTION DESCRIPTION","IRRUNL":"Hours Prod"})
routingkey1.reset_index(drop=True,inplace=True)

lookupforweekms1=pd.merge(lookupforweekms1,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms1 = lookupforweekms1.sort_values(by=['Hours Prod'])
lookupforweekms1.reset_index(drop=True,inplace=True)

lookupforweekms2=pd.merge(lookupforweekms2,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms2 = lookupforweekms2.sort_values(by=['Hours Prod'])
lookupforweekms2.reset_index(drop=True,inplace=True)

lookupforweekms3=pd.merge(lookupforweekms3,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms3 = lookupforweekms3.sort_values(by=['Hours Prod'])
lookupforweekms3.reset_index(drop=True,inplace=True)

lookupforweekms4=pd.merge(lookupforweekms4,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms4 = lookupforweekms4.sort_values(by=['Hours Prod'])
lookupforweekms4.reset_index(drop=True,inplace=True)

lookupforweekms5=pd.merge(lookupforweekms5,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms5 = lookupforweekms5.sort_values(by=['Hours Prod'])
lookupforweekms5.reset_index(drop=True,inplace=True)

lookupforweekms6=pd.merge(lookupforweekms6,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms6 = lookupforweekms6.sort_values(by=['Hours Prod'])
lookupforweekms6.reset_index(drop=True,inplace=True)

prodalert1 = lookupforweekms1[lookupforweekms1['Hours Prod'].isna()]
prodalert2 = lookupforweekms2[lookupforweekms2['Hours Prod'].isna()]
prodalert3 = lookupforweekms3[lookupforweekms3['Hours Prod'].isna()]
prodalert4 = lookupforweekms4[lookupforweekms4['Hours Prod'].isna()]
prodalert5 = lookupforweekms5[lookupforweekms5['Hours Prod'].isna()]
prodalert6 = lookupforweekms6[lookupforweekms6['Hours Prod'].isna()]
prodalert = prodalert1.append(prodalert2)
prodalert = prodalert.append(prodalert3)
prodalert = prodalert.append(prodalert4)
prodalert = prodalert.append(prodalert5)
prodalert = prodalert.append(prodalert6)

#prodalert.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\prodalert.xlsx')

In [22]:
#establish dataframe with metal shop routings for each component
routingkey1 = pd.read_sql_query('select * from KNL400A.JDEQUERY.ROUTSDLB',connection)
routingkey1 = routingkey1[['IRKITL','IRDSC1','IRRUNL']]
routingkey1['IRKITL'] = routingkey1['IRKITL'].apply(lambda x: x.strip())
routingkey1['IRRUNL'] = routingkey1['IRRUNL'].apply(lambda x: x/100)
routingkey1 = routingkey1.drop_duplicates(subset=['IRKITL','IRDSC1'])
routingkey1 = routingkey1.groupby(['IRKITL'],as_index=False).agg({'IRRUNL': 'sum'})
routingkey1 = routingkey1.rename(columns={"IRKITL":"COMPONENTS","IRDSC1":"ACTION DESCRIPTION","IRRUNL":"Hours Prod"})
routingkey1.reset_index(drop=True,inplace=True)

lookupforweekms7=pd.merge(lookupforweekms7,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms7 = lookupforweekms7.sort_values(by=['Hours Prod'])
lookupforweekms7.reset_index(drop=True,inplace=True)

lookupforweekms14=pd.merge(lookupforweekms14,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms14 = lookupforweekms14.sort_values(by=['Hours Prod'])
lookupforweekms14.reset_index(drop=True,inplace=True)

lookupforweekms21=pd.merge(lookupforweekms21,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms21 = lookupforweekms21.sort_values(by=['Hours Prod'])
lookupforweekms21.reset_index(drop=True,inplace=True)

prodalert1 = lookupforweekms7[lookupforweekms7['Hours Prod'].isna()]
prodalert2 = lookupforweekms14[lookupforweekms14['Hours Prod'].isna()]
prodalert3 = lookupforweekms21[lookupforweekms21['Hours Prod'].isna()]
prodalert = prodalert1.append(prodalert2)
prodalert = prodalert.append(prodalert3)
prodalert.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\prodalert.xlsx')
#prodalert.to_excel(r'T:\share\Thomas\prodalert.xlsx')

#multiply by qty

NameError: name 'lookupforweekms7' is not defined

In [30]:
#Number of MS components per color 
def comp_ms(lookupforweekms):

    lookupcomp = lookupforweekms.pivot_table(values='COMPONENT QTY',index=['COMPONENTS'],columns='COLOR',aggfunc=np.sum)
    lookupcomp=lookupcomp.fillna(0)

    lookupcomp.loc['Color Totals']= lookupcomp.sum(numeric_only=True, axis=0)
    lookupcomp.loc[:,'Component Totals'] = lookupcomp.sum(numeric_only=True, axis=1)

    pd.options.display.max_rows = 50000

    return lookupcomp

In [31]:
comp1 = comp_ms(lookupforweekms1)
comp2 = comp_ms(lookupforweekms2)
comp3 = comp_ms(lookupforweekms3)
comp4 = comp_ms(lookupforweekms4)
comp5 = comp_ms(lookupforweekms5)
comp6 = comp_ms(lookupforweekms6)

non_ms1 = list(set(paint1) ^ set(comp1.columns.tolist()))
paint1 = [e for e in paint1 if e not in non_ms1]
non_ms2 = list(set(paint2) ^ set(comp2.columns.tolist()))
paint2 = [e for e in paint2 if e not in non_ms2]
non_ms3 = list(set(paint3) ^ set(comp3.columns.tolist()))
paint3 = [e for e in paint3 if e not in non_ms3]
non_ms4 = list(set(paint4) ^ set(comp4.columns.tolist()))
paint4 = [e for e in paint4 if e not in non_ms4]
non_ms5 = list(set(paint5) ^ set(comp5.columns.tolist()))
paint15 = [e for e in paint5 if e not in non_ms5]
non_ms6 = list(set(paint6) ^ set(comp6.columns.tolist()))
paint21 = [e for e in paint6 if e not in non_ms6]

In [29]:
comp7 = comp_ms(lookupforweekms7)
comp14 = comp_ms(lookupforweekms14)
comp21 = comp_ms(lookupforweekms21)

non_ms7 = list(set(paint7) ^ set(comp7.columns.tolist()))
paint7 = [e for e in paint7 if e not in non_ms7]
non_ms14 = list(set(paint14) ^ set(comp14.columns.tolist()))
paint14 = [e for e in paint14 if e not in non_ms14]
non_ms21 = list(set(paint21) ^ set(comp21.columns.tolist()))
paint21 = [e for e in paint21 if e not in non_ms21]

In [40]:
#parsing through paintlist, find components with exclusive color runs, then mixed ones ; splits large component qtys
def shop_schedule(paintlist, lookupcomp):
    lookupcomp1 = lookupcomp
    comps = []
    amounts = []
    colors = [] 
    lookupcomp1 = lookupcomp1.drop('Color Totals')
    
    print('Truncated paintlist')
    
    for cur, nxt in zip(paintlist, paintlist[1:]):
        
        #if lookupcomp1['Component Totals'].sum() == 0:
                #break
            
        if lookupcomp1.empty == True:
            break;

        if cur in lookupcomp1.columns:
            lookupcomp1 = lookupcomp1.drop('Component Totals', axis=1)
            lookupcomp1.loc[:,'Component Totals'] = lookupcomp1.sum(numeric_only=True, axis=1)
            #print('Current Color')
            print(cur)
        
            #print(lookupcomp1)
            head = lookupcomp1.loc[lookupcomp1[cur] > 0]
            #print(head)
            head = head.loc[head[cur] == head['Component Totals']]
            
            
            #CHECK head empty due to no color run 
            print(head)
            
            while head.empty == False: 
                drop = head[cur].idxmax()
                top = head[cur].max()
                #comps.append([drop, 'All'])
                comps.append(drop)
                amounts.append(top)
                colors.append(cur)
                lookupcomp1 = lookupcomp1.drop(drop)
                head = head.drop(drop)
                #print(comps)
            
            #will hit if only multicolor components exist
            if head.empty == True: 
                head = lookupcomp1.loc[lookupcomp1[cur] > 0]
                next_run = head.loc[head[nxt] > 0]
                next_run = next_run[[cur,nxt,'Component Totals']]
                next_run.reset_index(level=0, inplace=True)
                next_run=pd.merge(next_run,routingkey1, how="left",on=['COMPONENTS'])
                next_run = next_run.set_index(['COMPONENTS'])
                next_run['Hours Prod'] = next_run['Hours Prod'] * (next_run['Component Totals'] - next_run[cur] - next_run[nxt])
                next_run = next_run.sort_values(by=['Hours Prod'])
                next_run['cur%'] = next_run[cur] / next_run['Component Totals']
                more_run = head.loc[head[nxt] == 0]
                more_run = more_run[[cur,'Component Totals']]
                more_run.reset_index(level=0, inplace=True)
                more_run=pd.merge(more_run,routingkey1, how="left",on=['COMPONENTS'])
                more_run = more_run.set_index(['COMPONENTS'])
                more_run['Hours Prod'] = more_run['Hours Prod'] * (more_run['Component Totals'] - more_run[cur])
                more_run = more_run.sort_values(by=['Hours Prod'])
                more_run['cur%'] = more_run[cur] / more_run['Component Totals']
                split_next = next_run.loc[next_run['Hours Prod'] > 1]
                split_more = more_run.loc[more_run['Hours Prod'] > 1]
                next_run = next_run.drop(split_next.index)
                more_run = more_run.drop(split_more.index)
                
                
                while next_run.empty == False:   
                    drop = next_run['cur%'].idxmax()
                    top = next_run[cur][next_run['cur%'].idxmax()]
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    next_run = next_run.drop(drop)
                    
                while split_next.empty == False:
                    drop = split_next['cur%'].idxmax()
                    row = split_next[split_next.index == drop]
                    number1 = row[cur]
                    number2 = row[nxt]
                    #comps.append([drop, int(number1), cur])
                    #comps.append([drop, int(number2), nxt])
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    comps.append(drop)
                    amounts.append(int(number2))
                    colors.append(nxt)
                    
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie[nxt] = headie[nxt] - number2
                    headie['Component Totals'] = headie['Component Totals'] - (number1 + number2)
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_next = split_next.drop(drop)
                    
                while more_run.empty == False:                             
                    drop = more_run['cur%'].idxmax()
                    top = more_run[cur][more_run['cur%'].idxmax()]
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    #print('morerun:')
                    #print(more_run)
                    #print(lookupcomp1)
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    more_run = more_run.drop(drop)
                    
                while split_more.empty == False:
                    drop = split_more['cur%'].idxmax()
                    row = split_more[split_more.index == drop]
                    number1 = row[cur]
                    #comps.append([drop, int(number1), cur])
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie['Component Totals'] = headie['Component Totals'] - number1
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_more = split_more.drop(drop)
                    
            #only multicolor
            if lookupcomp1[cur].sum() > 0:
                head = lookupcomp1.loc[lookupcomp1[cur] > 0]
                next_run = head.loc[head[nxt] > 0]
                #next_run = next_run.drop_duplicates()
                next_run = next_run[[cur,nxt,'Component Totals']]
                next_run.reset_index(level=0, inplace=True)
                next_run=pd.merge(next_run,routingkey1, how="left",on=['COMPONENTS'])
                next_run = next_run.set_index(['COMPONENTS'])
                next_run['Hours Prod'] = next_run['Hours Prod'] * (next_run['Component Totals'] - next_run[cur] - next_run[nxt])
                next_run = next_run.sort_values(by=['Hours Prod'])
                next_run['cur%'] = next_run[cur] / next_run['Component Totals']
                more_run = head.loc[head[nxt] == 0]
                more_run = more_run[[cur,'Component Totals']]
                more_run.reset_index(level=0, inplace=True)
                more_run=pd.merge(more_run,routingkey1, how="left",on=['COMPONENTS'])
                more_run = more_run.set_index(['COMPONENTS'])
                more_run['Hours Prod'] = more_run['Hours Prod'] * (more_run['Component Totals'] - more_run[cur])
                more_run = more_run.sort_values(by=['Hours Prod'])
                more_run['cur%'] = more_run[cur] / more_run['Component Totals']
                split_next = next_run.loc[next_run['Hours Prod'] > 1]
                split_more = more_run.loc[more_run['Hours Prod'] > 1]
                next_run = next_run.drop(split_next.index)
                more_run = more_run.drop(split_more.index)
                
                while next_run.empty == False:             
                    drop = next_run['cur%'].idxmax()
                    top = next_run[cur][next_run['cur%'].idxmax()]
                    #print(next_run)
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    next_run = next_run.drop(drop)
                
                while split_next.empty == False:
                    drop = split_next['cur%'].idxmax()
                    row = split_next[split_next.index == drop]
                    number1 = row[cur]
                    number2 = row[nxt]
                    #comps.append([drop, int(number1), cur])
                    #comps.append([drop, int(number2), nxt]) 
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    comps.append(drop)
                    amounts.append(int(number2))
                    colors.append(nxt)
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie[nxt] = headie[nxt] - number2
                    headie['Component Totals'] = headie['Component Totals'] - (number1 + number2)
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_next = split_next.drop(drop)
                    
                while more_run.empty == False:                             
                    drop = more_run['cur%'].idxmax()
                    top = more_run[cur][more_run['cur%'].idxmax()]
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    more_run = more_run.drop(drop)
                    
                while split_more.empty == False:
                    drop = split_more['cur%'].idxmax()
                    row = split_more[split_more.index == drop]
                    number1 = row[cur]
                    #comps.append([drop, int(number1), cur])
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie['Component Totals'] = headie['Component Totals'] - number1
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_more = split_more.drop(drop)
                    
            if lookupcomp1['Component Totals'].sum() == lookupcomp1[paintlist[-1]].sum():
                if lookupcomp1.empty == False:
                    print(paintlist[-1])
                    drop = lookupcomp1[paintlist[-1]].idxmax()
                    top = lookupcomp1[paintlist[-1]].max()
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(paintlist[-1])

                    lookupcomp1 = lookupcomp1.drop(drop)
    
    shopf1 = pd.DataFrame(comps)
    shopf2 = pd.DataFrame(amounts)
    shopf3 = pd.DataFrame(colors)
    shopframe = pd.concat([shopf1, shopf2, shopf3], axis = 1)
    
    return shopframe
    

In [37]:
print(paint5)

['EKT', 'N/A', 'E40', 'ET2', 'ERS', 'EJ67', 'EKS', 'EK5', 'EZ5', 'EFT', 'EHT', 'EMT', 'EDT', 'EJ0', 'EFS', 'EL9', 'EGX', 'EDS', 'E1T', '138', 'E58', 'EMS', 'EB7', 'EJ9', 'E0T', '146', 'EG2', 'E81', 'EK2', 'E1S', 'EK78', 'ED52', '120T', 'EHS', 'ELW', 'ESM', 'EK09', '120', 'EET', 'EK71']


In [41]:
shop1 = shop_schedule(paint1, comp1)
shop2 = shop_schedule(paint2, comp2)
shop3 = shop_schedule(paint3, comp3)
shop4 = shop_schedule(paint4, comp4)
shop5 = shop_schedule(paint5, comp5)
shop6 = shop_schedule(paint6, comp6)

Truncated paintlist
EKT
COLOR          120  120T  138  146  E0T  E1S  E1T  E40  E58  E81  EB7  ED52  \
COMPONENTS                                                                    
3AB12320495    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AB12510595    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AB15160395    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AB80810395    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AB80830295    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AB80840395    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AB81530395    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AJ416910300   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AJ416941100   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AJ416950700   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
5132B25H16     0.0   0.0  0.

<ipython-input-40-b6632a491196>:134: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-40-b6632a491196>:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie['Component Totals'] = headie['Component Totals'] - number1


N/A
COLOR         120  120T  138  146  E0T  E1S  E1T  E40  E58  E81  EB7  ED52  \
COMPONENTS                                                                   
1C5911301SA   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
1C5911304SA   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
1C5911307SA   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
1C5911309SA   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AA11260952   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
4AS111440     0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AJ129203P    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AJ417508P    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6TD401450297  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6TD401450897  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   

COLOR         EDS  EDT  EFS  EFT  EG2  EGX  EHS  EHT  EJ0  

<ipython-input-40-b6632a491196>:134: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-40-b6632a491196>:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie['Component Totals'] = headie['Component Totals'] - number1
<ipython-input-40-b6632a491196>:134: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydat

ERS
COLOR        120  120T  138  146  E0T  E1S  E1T  E40  E58  E81  EB7  ED52  \
COMPONENTS                                                                  
3AB10580295  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
5276D40H10   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
5278D02H01   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
5278D03H01   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
67839RS      0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA1136395   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA1136495   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA15090295  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA15520195  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA15520295  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA15520495  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.

...

<ipython-input-40-b6632a491196>:134: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-40-b6632a491196>:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie['Component Totals'] = headie['Component Totals'] - number1
<ipython-input-40-b6632a491196>:134: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydat

EHT
Empty DataFrame
Columns: [120, 120T, 138, 146, E0T, E1S, E1T, E40, E58, E81, EB7, ED52, EDS, EDT, EET, EFS, EFT, EG2, EGX, EHS, EHT, EJ0, EJ67, EJ9, EK5, EK71, EKS, EKT, EL9, EMS, EMT, ERS, ET2, EZ5, N/A, Component Totals]
Index: []
EMT
COLOR          120  120T  138  146  E0T  E1S  E1T  E40  E58  E81  EB7  ED52  \
COMPONENTS                                                                    
5130B79M19M    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
5282D59V01611  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA731901611   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA731902611   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   

COLOR          EDS  EDT  EET  EFS  EFT  EG2  EGX  EHS  EHT  EJ0  EJ67  EJ9  \
COMPONENTS                                                                   
5130B79M19M    0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
5282D59V01611  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

EGX
COLOR          120  120T  138  146  E0T  E1S  E1T  E40  E58  E81  EB7  ED52  \
COMPONENTS                                                                    
3AF40150795    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
5130B79M15M    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
5282D59V01612  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
6AA731901612   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3AF41820795    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   

COLOR          EDS  EDT  EET  EFS  EFT  EG2   EGX  EHS  EHT  EJ0  EJ67  EJ9  \
COMPONENTS                                                                    
3AF40150795    0.0  0.0  0.0  0.0  0.0  0.0  13.0  0.0  0.0  0.0   0.0  0.0   
5130B79M15M    0.0  0.0  0.0  0.0  0.0  0.0   1.0  0.0  0.0  0.0   0.0  0.0   
5282D59V01612  0.0  0.0  0.0  0.0  0.0  0.0  12.0  0.0  0.0  0.0   0.0  0.0   
6AA731901612   0.0  0.0  0.0  0.0  0.0  0.0   1

QG605410281CR               2.0  


KeyError: 'EK2'

In [31]:
#export MS schedules to excel files 
shop7 = shop_schedule(paint7, comp7)
shop14 = shop_schedule(paint14, comp14)
shop21 = shop_schedule(paint21, comp21)

Truncated paintlist
EFT
N/A

<ipython-input-30-fe785f86abcf>:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-30-fe785f86abcf>:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie['Component Totals'] = headie['Component Totals'] - number1



EKT


<ipython-input-30-fe785f86abcf>:95: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-30-fe785f86abcf>:96: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[nxt] = headie[nxt] - number2
<ipython-input-30-fe785f86abcf>:97: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

ET2
E40


...

EKS
EKT
EHT
ET2

<ipython-input-30-fe785f86abcf>:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-30-fe785f86abcf>:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie['Component Totals'] = headie['Component Totals'] - number1



EFT
EZ5
EK5


<ipython-input-30-fe785f86abcf>:95: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-30-fe785f86abcf>:96: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[nxt] = headie[nxt] - number2
<ipython-input-30-fe785f86abcf>:97: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

EFS
EJ0
EJ67
EDT
EMT
EL9
E1T
138
E0T
EGX
E58
EJ9
ED52
E1S
E81


In [32]:
#check entire inv download to see if there are sufficient number of components; if not, backtrace the WA and flag 
def check_shortage(lookupforweek): 
    
    lookupforweekcopy = lookupforweek
    lookupforweekcopy.reset_index(drop=True,inplace=True)
    
    #start with JDE download for current week
    if lookupforweekcopy['DATE'][0] <= friday0:
        location1 = pd.read_sql_query('select * from KNL400A.JDEQUERY.JDSINVEG20',connection)
        location1['ICC'] = location1['ICC'].apply(lambda x: x.strip())
        location1['IBLITM'] = location1['IBLITM'].apply(lambda x: x.strip())
        location1.reset_index(drop=True,inplace=True)
    #use modified inv for other two weeks
    else: 
        ##location1 = pd.read_excel('T:\share\Thomas\location1.xlsx')
        location1 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\location1.xlsx')
    
    #location1 = location
    flagged = []
    shortage = []
    ready = []
    
    n = range(len(lookupforweekcopy))
    
    for i in n:
        
        wa = lookupforweekcopy.loc[i]['WORK ORDER']
        component = lookupforweekcopy.loc[i]['COMPONENTS']
        amount = ((lookupforweekcopy.loc[i]['COMPONENT QTY'])/(lookupforweekcopy.loc[i]['INITIAL WA QTY'])) * lookupforweekcopy.loc[i]['OPEN PATTERN QTY']
        availability = location1['IBLITM'].str.contains(component).any()
        
        if availability == True:
            
            line = location1['LIPQOH'].loc[location1['IBLITM'] == component]
            stock = line.sum()
        
        
            #INVENTORY IS INSUFFICIENT
            if amount > stock: 
                #print(wa, component, amount, stock)
                flagged.append(wa)
                shortage.append(component)
                
            #INVENTORY IS SUFFICIENT    
            if amount <= stock:
                print('\n')
                print(component)
                for i in range(len(line)):
                    
                    totals = location1['LIPQOH'].loc[location1['IBLITM'] == component].iloc[i]
                    
                    if amount != 0:
                        print('stock')
                        print(totals)
                        print('amount1')
                        print(amount)
                        
                        #location1 = location1['LIPQOH'].loc[location1['IBLITM'] == component].iloc[i] - min(totals,amount)
                        #ocation1.loc[location1['IBLITM'] == component, 'LIPQOH'] -= min(totals,amount)
                        
                        otf = location1.loc[location1['IBLITM'] == component,'LIPQOH']
                        location1.at[otf.index[i],'LIPQOH'] -=min(totals,amount)
                        
                        
                        totals1 = location1['LIPQOH'].loc[location1['IBLITM'] == component].iloc[i]
                        print('totals1')
                        print(totals1)
                        
                        #location1 = location1['LIPQOH'].loc[location1['IBLITM'] == component].iloc[i] - min(totals,amount)
                        amount -= min(totals,amount)
                        if component in ready:
                            print('REPEAT')
                        ready.append(component)
                        print('amount2')
                        print(amount)
                    else:
                        break
                    
                #location1 = location1['']
                #print(wa)
                pass
            
        #NO INVENTORY FOUND
        else: 
            #print(wa, component)
            flagged.append(wa)
            shortage.append(component)  
    
    flagged = list(set(flagged))
    shortage = list(set(shortage))
    print('# Comps short')
    print((shortage))
    
    #location1.to_excel(r'T:\share\Thomas\location1.xlsx')
    location1.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\location1.xlsx')
    
    compframe = pd.DataFrame(shortage, columns=['COMPONENTS'])
    
    return flagged, compframe

In [6]:
#CHANGE WEEK FILTERING AND POTENTIALLY SUBTRACTION: ONLY CHECKING EVERY OTHER WEEK
timer10 = time.perf_counter()
print("Matching inventory 1/6...")
flagged1, shortage1 = check_shortage(allcomps1)
print("Matching inventory 2/6...")
flagged2, shortage2 = check_shortage(allcomps2)
print("Matching inventory 3/6...")
flagged3, shortage3 = check_shortage(allcomps3)
print("Matching inventory 4/6...")
flagged4, shortage4 = check_shortage(allcomps4)
print("Matching inventory 5/6...")
flagged5, shortage5 = check_shortage(allcomps5)
print("Matching inventory 6/6...")
flagged6, shortage6 = check_shortage(allcomps6)
timer11 = time.perf_counter()
print("Inventory check complete. Load time:")
print(timer11 - timer10)

NameError: name 'timer' is not defined

In [ ]:
#append vendor back to the appropriate component, and export all to excel 
shortage1=pd.merge(shortage1,vendkey,how="left",on="COMPONENTS")
shortage2=pd.merge(shortage2,vendkey,how="left",on="COMPONENTS")
shortage3=pd.merge(shortage3,vendkey,how="left",on="COMPONENTS")
shortage4=pd.merge(shortage4,vendkey,how="left",on="COMPONENTS")
shortage5=pd.merge(shortage5,vendkey,how="left",on="COMPONENTS")
shortage6=pd.merge(shortage6,vendkey,how="left",on="COMPONENTS")
shortage1['Supplier']=shortage1['Supplier'].fillna('ERROR')
shortage2['Supplier']=shortage2['Supplier'].fillna('ERROR')
shortage3['Supplier']=shortage3['Supplier'].fillna('ERROR')
shortage4['Supplier']=shortage4['Supplier'].fillna('ERROR')
shortage5['Supplier']=shortage5['Supplier'].fillna('ERROR')
shortage6['Supplier']=shortage6['Supplier'].fillna('ERROR')
shortage1.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
shortage2.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
shortage3.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
shortage4.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
shortage5.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
shortage6.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
#shortage7.to_excel(r'T:\share\Thomas\shortage7.xlsx')
#shortage14.to_excel(r'T:\share\Thomas\shortage14.xlsx')
#shortage21.to_excel(r'T:\share\Thomas\shortage21.xlsx')
#shortage7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shortage7.xlsx')
#shortage14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shortage14.xlsx')
#shortage21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shortage21.xlsx')

In [ ]:
#put all of the WA ready for execution into new dataframe; can then feed into all logic for dynamic updating 
allcompsadj1 = allcomps1[~allcomps1['WORK ORDER'].isin(flagged1)]
allcompsadj1.reset_index(drop=True,inplace=True)
allcompsadj2 = allcomps2[~allcomps2['WORK ORDER'].isin(flagged2)]
allcompsadj2.reset_index(drop=True,inplace=True)
allcompsadj3 = allcomps3[~allcomps3['WORK ORDER'].isin(flagged3)]
allcompsadj3.reset_index(drop=True,inplace=True)
allcompsadj4 = allcomps1[~allcomps4['WORK ORDER'].isin(flagged4)]
allcompsadj4.reset_index(drop=True,inplace=True)
allcompsadj5 = allcomps2[~allcomps5['WORK ORDER'].isin(flagged5)]
allcompsadj5.reset_index(drop=True,inplace=True)
allcompsadj6 = allcomps3[~allcomps6['WORK ORDER'].isin(flagged6)]
allcompsadj6.reset_index(drop=True,inplace=True)

noworkcomps1 = allcomps1[allcomps1['WORK ORDER'].isin(flagged1)]
noworkcomps1.reset_index(drop=True,inplace=True)
noworkforweek1 = noworkcomps1.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
noworkforweek1 = noworkforweek1.sort_values(by=['Hours Work'])

lookupforweekadj1 = allcompsadj1.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj1 = lookupforweekadj1.sort_values(by=['Hours Work'])
lookupforweekadj1.reset_index(drop=True,inplace=True)
lookupforweekadj2 = allcompsadj2.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj2 = lookupforweekadj2.sort_values(by=['Hours Work'])
lookupforweekadj2.reset_index(drop=True,inplace=True)
lookupforweekadj3 = allcompsadj3.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj3 = lookupforweekadj3.sort_values(by=['Hours Work'])
lookupforweekadj3.reset_index(drop=True,inplace=True)
lookupforweekadj4 = allcompsadj4.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj4 = lookupforweekadj4.sort_values(by=['Hours Work'])
lookupforweekadj4.reset_index(drop=True,inplace=True)
lookupforweekadj5 = allcompsadj5.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj5 = lookupforweekadj5.sort_values(by=['Hours Work'])
lookupforweekadj5.reset_index(drop=True,inplace=True)
lookupforweekadj6 = allcompsadj6.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj6 = lookupforweekadj6.sort_values(by=['Hours Work'])
lookupforweekadj6.reset_index(drop=True,inplace=True)

In [ ]:
mpfadj1 = mpf_assy(lookupforweekadj1)
coladj1 = col_assy(lookupforweekadj1)
mpfadj2 = mpf_assy(lookupforweekadj2)
coladj2 = col_assy(lookupforweekadj2)
mpfadj3 = mpf_assy(lookupforweekadj3)
coladj3 = col_assy(lookupforweekadj3)
mpfadj4 = mpf_assy(lookupforweekadj4)
coladj4 = col_assy(lookupforweekadj4)
mpfadj5 = mpf_assy(lookupforweekadj5)
coladj5 = col_assy(lookupforweekadj5)
mpfadj6 = mpf_assy(lookupforweekadj6)
coladj6 = col_assy(lookupforweekadj6)

#mpfadj7.to_excel('T:\share\Thomas\mpfadj7.xlsx')
#coladj7.to_excel('T:\share\Thomas\coladj7.xlsx')
#mpfadj14.to_excel('T:\share\Thomas\mpfadj14.xlsx')
#coladj14.to_excel('T:\share\Thomas\coladj14.xlsx')
#mpfadj21.to_excel('T:\share\Thomas\mpfadj21.xlsx')
#coladj21.to_excel('T:\share\Thomas\coladj21.xlsx')
mpfadj7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpfadj7.xlsx')
coladj7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coladj7.xlsx')
mpfadj14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpfadj14.xlsx')
coladj14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coladj14.xlsx')
mpfadj21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpfadj21.xlsx')
coladj21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coladj21.xlsx')

In [ ]:
paintadj1 = paint_schedule(mpfadj1, coladj1)
paintadj2 = paint_schedule(mpfadj2, coladj2)
paintadj3 = paint_schedule(mpfadj3, coladj3)
paintadj4 = paint_schedule(mpfadj4, coladj4)
paintadj5 = paint_schedule(mpfadj5, coladj5)
paintadj6 = paint_schedule(mpfadj6, coladj6)

In [ ]:
work_glass = pd.DataFrame()
work_legs = pd.DataFrame()
work_paintpack = pd.DataFrame()
work_rockwell = pd.DataFrame()
work_station50 = pd.DataFrame()
work_sysassy = pd.DataFrame()
work_tables = pd.DataFrame()
nowork_glass = pd.DataFrame()
nowork_legs = pd.DataFrame()
nowork_paintpack = pd.DataFrame()
nowork_rockwell = pd.DataFrame()
nowork_station50 = pd.DataFrame()
nowork_sysassy = pd.DataFrame()
nowork_tables = pd.DataFrame()

lookupforweekadj7x = lookupforweekadj1[['MPF','DATE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SO TYPE','SALES ORDER','WORK ORDER','SALES LINE','COLOR','AREA']]
noworkforweek7x = noworkforweek1[['MPF','DATE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SO TYPE','SALES ORDER','WORK ORDER','SALES LINE','COLOR','AREA']]

gl_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Glass']
gl_yes = gl_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
lg_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Legs']
lg_yes = lg_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
pp_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Paint/Pack']
pp_yes = pp_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
ro_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Rockwell']
ro_yes = ro_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
s5_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Station 50']
s5_yes = s5_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
sy_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Sys Assy']
sy_yes = sy_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
ta_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Tables']
ta_yes = ta_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
    
gl_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Glass']
gl_no = gl_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
lg_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Legs']
lg_no = lg_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
pp_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Paint/Pack']
pp_no = pp_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
ro_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Rockwell']
ro_no = ro_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
s5_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Station 50']
s5_no = s5_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
sy_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Sys Assy']
sy_no = sy_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
ta_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Tables']
ta_no = ta_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
    
for i in range(len(paintadj1)):

    appendthis1 = gl_yes[gl_yes['COLOR'] == paintadj1[i]]
    work_glass = work_glass.append(appendthis1)
    work_glass.reset_index(drop=True,inplace=True)
    appendthis2 = lg_yes[lg_yes['COLOR'] == paintadj1[i]]
    work_legs = work_legs.append(appendthis2)
    work_legs.reset_index(drop=True,inplace=True)
    appendthis3 = pp_yes[pp_yes['COLOR'] == paintadj1[i]]
    work_paintpack = work_paintpack.append(appendthis3)
    work_paintpack.reset_index(drop=True,inplace=True)
    appendthis4 = ro_yes[ro_yes['COLOR'] == paintadj1[i]]
    work_rockwell = work_rockwell.append(appendthis4)
    work_rockwell.reset_index(drop=True,inplace=True)
    appendthis5 = s5_yes[s5_yes['COLOR'] == paintadj1[i]]
    work_station50 = work_station50.append(appendthis5)
    work_station50.reset_index(drop=True,inplace=True)
    appendthis6 = sy_yes[sy_yes['COLOR'] == paintadj1[i]]
    work_sysassy = work_sysassy.append(appendthis6)
    work_sysassy.reset_index(drop=True,inplace=True)
    appendthis7 = ta_yes[ta_yes['COLOR'] == paintadj1[i]]
    work_tables = work_tables.append(appendthis7)
    work_tables.reset_index(drop=True,inplace=True)
        
    appendthis8 = gl_no[gl_no['COLOR'] == paintadj1[i]]
    nowork_glass = nowork_glass.append(appendthis8)
    nowork_glass.reset_index(drop=True,inplace=True)
    appendthis9 = lg_no[lg_no['COLOR'] == paintadj1[i]]
    nowork_legs = nowork_legs.append(appendthis9)
    nowork_legs.reset_index(drop=True,inplace=True)
    appendthis10 = pp_no[pp_no['COLOR'] == paintadj1[i]]
    nowork_paintpack = nowork_paintpack.append(appendthis10)
    nowork_paintpack.reset_index(drop=True,inplace=True)
    appendthis11 = ro_no[ro_no['COLOR'] == paintadj1[i]]
    nowork_rockwell = nowork_rockwell.append(appendthis11)
    nowork_rockwell.reset_index(drop=True,inplace=True)
    appendthis12 = s5_no[s5_no['COLOR'] == paintadj1[i]]
    nowork_station50 = nowork_station50.append(appendthis12)
    nowork_station50.reset_index(drop=True,inplace=True)
    appendthis13 = sy_no[sy_no['COLOR'] == paintadj1[i]]
    nowork_sysassy = nowork_sysassy.append(appendthis13)
    nowork_sysassy.reset_index(drop=True,inplace=True)
    appendthis14 = ta_no[ta_no['COLOR'] == paintadj1[i]]
    nowork_tables = nowork_tables.append(appendthis14)
    nowork_tables.reset_index(drop=True,inplace=True)
        
#work_glass.to_excel(r'T:\share\Thomas\work_glass.xlsx')
#work_legs.to_excel(r'T:\share\Thomas\work_legs.xlsx')
#work_paintpack.to_excel(r'T:\share\Thomas\work_paintpack.xlsx')
#work_rockwell.to_excel(r'T:\share\Thomas\work_rockwell.xlsx')
#work_station50.to_excel(r'T:\share\Thomas\work_station50.xlsx')
#work_sysassy.to_excel(r'T:\share\Thomas\work_sysassy.xlsx')
#work_tables.to_excel(r'T:\share\Thomas\work_tables.xlsx')
#nowork_glass.to_excel(r'T:\share\Thomas\nowork_glass.xlsx')
#nowork_legs.to_excel(r'T:\share\Thomas\nowork_legs.xlsx')
#nowork_paintpack.to_excel(r'T:\share\Thomas\nowork_paintpack.xlsx')
#nowork_rockwell.to_excel(r'T:\share\Thomas\nowork_rockwell.xlsx')
#nowork_station50.to_excel(r'T:\share\Thomas\nowork_station50.xlsx')
#nowork_sysassy.to_excel(r'T:\share\Thomas\nowork_sysassy.xlsx')
#nowork_tables.to_excel(r'T:\share\Thomas\nowork_tables.xlsx')

work_glass.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_glass.xlsx')
work_legs.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_legs.xlsx')
work_paintpack.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_paintpack.xlsx')
work_rockwell.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_rockwell.xlsx')
work_station50.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_station50.xlsx')
work_sysassy.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_sysassy.xlsx')
work_tables.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_tables.xlsx')
nowork_glass.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_glass.xlsx')
nowork_legs.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_legs.xlsx')
nowork_paintpack.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_paintpack.xlsx')
nowork_rockwell.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_rockwell.xlsx')
nowork_station50.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_station50.xlsx')
nowork_sysassy.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_sysassy.xlsx')
nowork_tables.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_tables.xlsx')

In [ ]:
paintframeadj1 = pd.DataFrame(paintadj1)
paintframeadj1 = paintframeadj1[paintframeadj1[0] != 'N/A']
paintframeadj1.reset_index()
#paintframeadj7.to_excel('T:\share\Thomas\paintframeadj7.xlsx')
#ATTENTIONNNNNNNNNNNNNNNNNNNNpaintframeadj1.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj1.xlsx')
paintframeadj2 = pd.DataFrame(paintadj2)
paintframeadj2 = paintframeadj2[paintframeadj2[0] != 'N/A']
paintframeadj2.reset_index()
#paintframeadj14.to_excel('T:\share\Thomas\paintframeadj14.xlsx')
paintframeadj2.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj14.xlsx')
paintframeadj3 = pd.DataFrame(paintadj3)
paintframeadj3 = paintframeadj3[paintframeadj3[0] != 'N/A']
paintframeadj3.reset_index()
#paintframeadj21.to_excel('T:\share\Thomas\paintframeadj21.xlsx')
paintframeadj3.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj21.xlsx')
paintframeadj4 = pd.DataFrame(paintadj4)
paintframeadj4 = paintframeadj4[paintframeadj4[0] != 'N/A']
paintframeadj4.reset_index()
#paintframeadj21.to_excel('T:\share\Thomas\paintframeadj21.xlsx')
paintframeadj4.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj21.xlsx')
paintframeadj5 = pd.DataFrame(paintadj5)
paintframeadj5 = paintframeadj5[paintframeadj5[0] != 'N/A']
paintframeadj5.reset_index()
#paintframeadj21.to_excel('T:\share\Thomas\paintframeadj21.xlsx')
paintframeadj5.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj21.xlsx')
paintframeadj6 = pd.DataFrame(paintadj6)
paintframeadj6 = paintframeadj6[paintframeadj6[0] != 'N/A']
paintframeadj6.reset_index()
#paintframeadj21.to_excel('T:\share\Thomas\paintframeadj21.xlsx')
paintframeadj6.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj21.xlsx')

In [ ]:
lookupforweekmsadj1 = create_lookupms(allcompsadj1, paintadj1)
lookupforweekmsadj2 = create_lookupms(allcompsadj2, paintadj2)
lookupforweekmsadj3 = create_lookupms(allcompsadj3, paintadj3)
lookupforweekmsadj4 = create_lookupms(allcompsadj4, paintadj4)
lookupforweekmsadj5 = create_lookupms(allcompsadj5, paintadj5)
lookupforweekmsadj6 = create_lookupms(allcompsadj6, paintadj6)

In [ ]:
lookupforweekmsadj1=pd.merge(lookupforweekmsadj1,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj1 = lookupforweekmsadj1.sort_values(by=['Hours Prod'])
lookupforweekmsadj1.reset_index(drop=True,inplace=True)
lookupforweekmsadj2=pd.merge(lookupforweekmsadj2,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj2 = lookupforweekmsadj2.sort_values(by=['Hours Prod'])
lookupforweekmsadj2.reset_index(drop=True,inplace=True)
lookupforweekmsadj3=pd.merge(lookupforweekmsadj3,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj3 = lookupforweekmsadj3.sort_values(by=['Hours Prod'])
lookupforweekmsadj3.reset_index(drop=True,inplace=True)
lookupforweekmsadj4=pd.merge(lookupforweekmsadj4,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj4 = lookupforweekmsadj4.sort_values(by=['Hours Prod'])
lookupforweekmsadj4.reset_index(drop=True,inplace=True)
lookupforweekmsadj5=pd.merge(lookupforweekmsadj5,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj5 = lookupforweekmsadj5.sort_values(by=['Hours Prod'])
lookupforweekmsadj5.reset_index(drop=True,inplace=True)
lookupforweekmsadj6=pd.merge(lookupforweekmsadj6,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj6 = lookupforweekmsadj6.sort_values(by=['Hours Prod'])
lookupforweekmsadj6.reset_index(drop=True,inplace=True)

In [ ]:
compadj1 = comp_ms(lookupforweekmsadj1)
compadj2 = comp_ms(lookupforweekmsadj2)
compadj3 = comp_ms(lookupforweekmsadj3)
compadj4 = comp_ms(lookupforweekmsadj4)
compadj5 = comp_ms(lookupforweekmsadj5)
compadj6 = comp_ms(lookupforweekmsadj6)

non_msadj1 = list(set(paintadj1) ^ set(compadj1.columns.tolist()))
paintadj1 = [e for e in paintadj1 if e not in non_msadj1]
non_msadj2 = list(set(paintadj2) ^ set(compadj2.columns.tolist()))
paintadj2 = [e for e in paintadj2 if e not in non_msadj2]
non_msadj3 = list(set(paintadj3) ^ set(compadj3.columns.tolist()))
paintadj3 = [e for e in paintadj3 if e not in non_msadj3]

In [ ]:
shopadj7 = shop_schedule(paintadj7, compadj7)
shopadj14 = shop_schedule(paintadj14, compadj14)
shopadj21 = shop_schedule(paintadj21, compadj21)
#shopadj7.to_excel('T:\share\Thomas\shopadj7.xlsx')
#shopadj14.to_excel('T:\share\Thomas\shopadj14.xlsx')
#shopadj21.to_excel('T:\share\Thomas\shopadj21.xlsx')
shopadj7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shopadj7.xlsx')
shopadj14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shopadj14.xlsx')
shopadj21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shopadj21.xlsx')

In [ ]:
###END OF CODE 

In [33]:
#retrieve flagged WA numbers and components with shortages 
timer3 = time.perf_counter()
print("Matching inventory. ~5 min wait time remaining")
flagged7, shortage7 = check_shortage(allcomps7)
print("Current week inventory check complete. ~4 min wait time remaining")
flagged14, shortage14 = check_shortage(allcomps14)
print("Next week inventory check complete. ~2 min wait time remaining")
flagged21, shortage21 = check_shortage(allcomps21)
timer4 = time.perf_counter()
print("load time:")
print(timer4 - timer3)

Matching inventory. ~5 min wait time remaining


T5131B96H02
stock
2.0
amount1
39.0
totals1
0.0
amount2
37.0
stock
16.0
amount1
37.0
totals1
0.0
REPEAT
amount2
21.0
stock
40.0
amount1
21.0
totals1
19.0
REPEAT
amount2
0.0


1A52729G01
stock
53.0
amount1
39.0
totals1
14.0
amount2
0.0


ORBKTPMDVP
stock
411.0
amount1
14.0
totals1
397.0
amount2
0.0


ORCHBLINSRT
stock
59070.0
amount1
840.0
totals1
58230.0
amount2
0.0


1B5402052
stock
126.0
amount1
14.0
totals1
112.0
amount2
0.0


ORBKTPMDVP
stock
397.0
amount1
4.0
totals1
393.0
REPEAT
amount2
0.0


ORCHBLINSRT
stock
58230.0
amount1
192.0
totals1
58038.0
REPEAT
amount2
0.0


1B5402052
stock
112.0
amount1
4.0
totals1
108.0
REPEAT
amount2
0.0


ORCHBLINSRT
stock
58038.0
amount1
60.0
totals1
57978.0
REPEAT
amount2
0.0


1B5402052
stock
108.0
amount1
1.0
totals1
107.0
REPEAT
amount2
0.0


ORBKTPMDVP
stock
393.0
amount1
1.0
totals1
392.0
REPEAT
amount2
0.0


ORCHBLINSRT
stock
57978.0
amount1
120.0
totals1
57858.0
REPEAT
amount2
0.0


1B5402052




1B5402052
stock
25.0
amount1
73.0
totals1
0.0
REPEAT
amount2
48.0
stock
3600.0
amount1
48.0
totals1
3552.0
REPEAT
amount2
0.0


ORCHBLINSRT
stock
52770.0
amount1
7008.0
totals1
45762.0
REPEAT
amount2
0.0


3AB12051395
stock
1.0
amount1
1.0
totals1
0.0
amount2
0.0


3AB120695
stock
37.0
amount1
2.0
totals1
35.0
amount2
0.0


3AB120795
stock
2818.0
amount1
1.0
totals1
2817.0
amount2
0.0


3AE411395
stock
822.0
amount1
6.0
totals1
816.0
REPEAT
amount2
0.0


3AB448395
stock
990.0
amount1
6.0
totals1
984.0
REPEAT
amount2
0.0


3AE411395
stock
816.0
amount1
160.0
totals1
656.0
REPEAT
amount2
0.0


3AB448395
stock
984.0
amount1
80.0
totals1
904.0
REPEAT
amount2
0.0


3AB448395
stock
904.0
amount1
80.0
totals1
824.0
REPEAT
amount2
0.0


ORCHBLINSRT
stock
45762.0
amount1
7680.0
totals1
38082.0
REPEAT
amount2
0.0


1B5402052
stock
0.0
amount1
80.0
totals1
0.0
REPEAT
amount2
80.0
stock
3552.0
amount1
80.0
totals1
3472.0
REPEAT
amount2
0.0


ORBKTPMDVP
stock
237.0
amount1
80.0
totals1
157.0
REPE



1A52740H01
stock
2002.488
amount1
1.0
totals1
2001.488
amount2
0.0


5132B10H03
stock
580.0
amount1
1.0
totals1
579.0
amount2
0.0


7737C65H02
stock
9.0
amount1
2.0
totals1
7.0
amount2
0.0


2668A03H01
stock
40650.0
amount1
4.0
totals1
40646.0
amount2
0.0


5282D55H01
stock
2819.0
amount1
8.0
totals1
2811.0
amount2
0.0


6AA722952
stock
274.0
amount1
2.0
totals1
272.0
amount2
0.0


1A52739H01
stock
5296.0
amount1
14.0
totals1
5282.0
amount2
0.0


1A52747H01
stock
940.0
amount1
8.0
totals1
932.0
amount2
0.0


1A52746H01
stock
2672.0
amount1
4.0
totals1
2668.0
amount2
0.0


5282D63H01
stock
390.0
amount1
4.0
totals1
386.0
amount2
0.0


1A52394H01
stock
968.0
amount1
8.0
totals1
960.0
amount2
0.0


5282D60G01
stock
506.0
amount1
2.0
totals1
504.0
amount2
0.0


7737C58V04GL13
stock
1.0
amount1
1.0
totals1
0.0
amount2
0.0


1A52394H01
stock
960.0
amount1
4.0
totals1
956.0
REPEAT
amount2
0.0


6AA455796
stock
867.0
amount1
1.0
totals1
866.0
amount2
0.0


5132B10H03
stock
579.0
amount1
3.0


1.0
totals1
555.0
amount2
0.0


7100100
stock
6776.0
amount1
4.0
totals1
6772.0
amount2
0.0


5128B44G01
stock
4780.0
amount1
4.0
totals1
4776.0
REPEAT
amount2
0.0


6AA457200
stock
9925.17
amount1
5.0
totals1
9920.17
REPEAT
amount2
0.0


5128B42V61TEMP
stock
6.0
amount1
2.0
totals1
4.0
amount2
0.0


6AA457200
stock
9920.17
amount1
16.0
totals1
9904.17
REPEAT
amount2
0.0


5128B44G01
stock
4776.0
amount1
10.0
totals1
4766.0
REPEAT
amount2
0.0


5128B44G01
stock
4766.0
amount1
20.0
totals1
4746.0
REPEAT
amount2
0.0


6AA457200
stock
9904.17
amount1
40.0
totals1
9864.17
REPEAT
amount2
0.0


5128B42V25TEMP
stock
139.0
amount1
10.0
totals1
129.0
amount2
0.0


5128B44G01
stock
4746.0
amount1
12.0
totals1
4734.0
REPEAT
amount2
0.0


6AA457200
stock
9864.17
amount1
17.0
totals1
9847.17
REPEAT
amount2
0.0


5128B42V112TEMP
stock
9.0
amount1
4.0
totals1
5.0
amount2
0.0


6AA457200
stock
9847.17
amount1
7.0
totals1
9840.17
REPEAT
amount2
0.0


5128B42V61TEMP
stock
4.0
amount1
3.0
totals1
1.0
REP



2MA2979H01
stock
339.0
amount1
4.0
totals1
335.0
REPEAT
amount2
0.0


3TA4046
stock
3987.0
amount1
12.0
totals1
3975.0
REPEAT
amount2
0.0


2TP40363
stock
432.0
amount1
4.0
totals1
428.0
REPEAT
amount2
0.0


3AE411395
stock
416.0
amount1
2.0
totals1
414.0
REPEAT
amount2
0.0


3AF504300
stock
10.0
amount1
1.0
totals1
9.0
amount2
0.0


3AE411395
stock
414.0
amount1
2.0
totals1
412.0
REPEAT
amount2
0.0


3AF504300
stock
9.0
amount1
1.0
totals1
8.0
REPEAT
amount2
0.0


3AE411395
stock
412.0
amount1
2.0
totals1
410.0
REPEAT
amount2
0.0


3AE000595
stock
16.0
amount1
1.0
totals1
15.0
amount2
0.0


1B533070295
stock
4.0
amount1
1.0
totals1
3.0
amount2
0.0


3AE411395
stock
410.0
amount1
2.0
totals1
408.0
REPEAT
amount2
0.0


3AE000595
stock
15.0
amount1
1.0
totals1
14.0
REPEAT
amount2
0.0


1B533070295
stock
3.0
amount1
1.0
totals1
2.0
REPEAT
amount2
0.0


3AE411395
stock
408.0
amount1
2.0
totals1
406.0
REPEAT
amount2
0.0


3AE000595
stock
14.0
amount1
1.0
totals1
13.0
REPEAT
amount2
0.0




...

6.0
totals1
0.0
REPEAT
amount2
6.0
stock
0.0
amount1
6.0
totals1
0.0
REPEAT
amount2
6.0
stock
0.0
amount1
6.0
totals1
0.0
REPEAT
amount2
6.0
stock
116.0
amount1
6.0
totals1
110.0
REPEAT
amount2
0.0


1A52678G02
stock
84.0
amount1
3.0
totals1
81.0
REPEAT
amount2
0.0


5128B01G01
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
41.0
amount1
3.0
totals1
38.0
REPEAT
amount2
0.0


7735C76H01
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
110.0
amount1
2.0
totals1
108.0
REPEAT
amount2
0.0


7736C31H01
stock
0.0
amount1
1.0
totals1
0.0
REPEAT
amount2
1.0
stock
38.0
amount1
1.0
totals1
37.0
REPEAT
amount2
0.0


1A52678G04
stock
349.0
amount1
1.0
totals1
348.0




6AJ4067
stock
0.0
amount1
20.0
totals1
0.0
amount2
20.0
stock
2572.0
amount1
20.0
totals1
2552.0
REPEAT
amount2
0.0


5128B01G01
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
38.0
amount1
3.0
totals1
35.0
REPEAT
amount2
0.0


7735C76H01
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
108.0
amount1
2.0
totals1
106.0
REPEAT
amount2
0.0


7736C31H01
stock
0.0
amount1
1.0
totals1
0.0
REPEAT
amount2
1.0
stock
37.0
amount1
1.0
totals1
36.0
REPEAT
amount2
0.0


1A52678G04
stock
348.0
amount1
1.0
totals1
347.0
REPEAT
amount2
0.0


3AB801003115
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
0.

0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
29.0
amount1
2.0
totals1
27.0
REPEAT
amount2
0.0


1A52678G01
stock
320.0
amount1
2.0
totals1
318.0
REPEAT
amount2
0.0


3AB10170195
stock
0.0
amount1
10.0
totals1
0.0
REPEAT
amount2
10.0
stock
62.0
amount1
10.0
totals1
52.0
REPEAT
amount2
0.0


6AA506496
stock
15.0
amount1
5.0
totals1
10.0
REPEAT
amount2
0.0


6AA502596
stock
0.0
amount1
5.0
totals1
0.0
REPEAT
amount2
5.0
stock
0.0
amount1
5.0
totals1
0.0
REPEAT
amount2
5.0
stock
70.0
amount1
5.0
totals1
65.0
REPEAT
amount2
0.0


3AB10170195
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
52.0
amount1
2.0
totals1
50.0
REPEAT
amount2
0.0


6AA506496
stock
10.0
amount1
1.0
totals1
9.0
REPEAT
amount2
0.0


6AA502596
stock
0.0
amount1
1.0
totals1
0.0
REPEAT
amount2
1.



5128B45G01
stock
77.0
amount1
1.0
totals1
76.0
REPEAT
amount2
0.0


3AB401252
stock
0.0
amount1
2.0
totals1
0.0
REPEAT
amount2
2.0
stock
3027.0
amount1
2.0
totals1
3025.0
REPEAT
amount2
0.0


7196440
stock
20468.0
amount1
2.0
totals1
20466.0
REPEAT
amount2
0.0


3AB400095
stock
10146.0
amount1
4.0
totals1
10142.0
REPEAT
amount2
0.0


3AB405900
stock
6913.0
amount1
4.0
totals1
6909.0
REPEAT
amount2
0.0


3AB406000
stock
2473.0
amount1
4.0
totals1
2469.0
REPEAT
amount2
0.0


3AB418700
stock
264.0
amount1
2.0
totals1
262.0
REPEAT
amount2
0.0


3AB400495
stock
0.0
amount1
4.0
totals1
0.0
REPEAT
amount2
4.0
stock
0.0
amount1
4.0
totals1
0.0
REPEAT
amount2
4.0
stock
0.0
amount1
4.0
totals1
0.0
REPEAT
amount2
4.0
stock
476.0
amount1
4.0
totals1
472.0
REPEAT
amount2
0.0


3AB802595
stock
0.0
amount1
3.0
totals1
0.0
REPEAT
amount2
3.0
stock
130.0
amount1
3.0
totals1
127.0
REPEAT
amount2
0.0


6AA450140
stock
27423.0
amount1
24.0
totals1
27399.0
REPEAT
amount2
0.0


3AB401252
stock
0.0
amount1

PermissionError: [Errno 13] Permission denied: '\\\\knl4prd-efs01\\Tableau\\obot\\PaintlineSched\\location1.xlsx'

In [20]:
#append vendor back to the appropriate component, and export all to excel 
shortage7=pd.merge(shortage7,vendkey,how="left",on="COMPONENTS")
shortage14=pd.merge(shortage14,vendkey,how="left",on="COMPONENTS")
shortage21=pd.merge(shortage21,vendkey,how="left",on="COMPONENTS")
shortage7['Supplier']=shortage7['Supplier'].fillna('ERROR')
shortage14['Supplier']=shortage14['Supplier'].fillna('ERROR')
shortage21['Supplier']=shortage21['Supplier'].fillna('ERROR')
shortage7.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
shortage14.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
shortage21.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)
#shortage7.to_excel(r'T:\share\Thomas\shortage7.xlsx')
#shortage14.to_excel(r'T:\share\Thomas\shortage14.xlsx')
#shortage21.to_excel(r'T:\share\Thomas\shortage21.xlsx')
shortage7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shortage7.xlsx')
shortage14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shortage14.xlsx')
shortage21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shortage21.xlsx')

In [21]:
#put all of the WA ready for execution into new dataframe; can then feed into all logic for dynamic updating 
allcompsadj7 = allcomps7[~allcomps7['WORK ORDER'].isin(flagged7)]
allcompsadj7.reset_index(drop=True,inplace=True)
allcompsadj14 = allcomps14[~allcomps14['WORK ORDER'].isin(flagged14)]
allcompsadj14.reset_index(drop=True,inplace=True)
allcompsadj21 = allcomps21[~allcomps21['WORK ORDER'].isin(flagged21)]
allcompsadj21.reset_index(drop=True,inplace=True)

noworkcomps7 = allcomps7[allcomps7['WORK ORDER'].isin(flagged7)]
noworkcomps7.reset_index(drop=True,inplace=True)
noworkforweek7 = noworkcomps7.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
noworkforweek7 = noworkforweek7.sort_values(by=['Hours Work'])

lookupforweekadj7 = allcompsadj7.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj7 = lookupforweekadj7.sort_values(by=['Hours Work'])
lookupforweekadj7.reset_index(drop=True,inplace=True)
lookupforweekadj14 = allcompsadj14.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj14 = lookupforweekadj14.sort_values(by=['Hours Work'])
lookupforweekadj14.reset_index(drop=True,inplace=True)
lookupforweekadj21 = allcompsadj21.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweekadj21 = lookupforweekadj21.sort_values(by=['Hours Work'])
lookupforweekadj21.reset_index(drop=True,inplace=True)

In [22]:
mpfadj7 = mpf_assy(lookupforweekadj7)
coladj7 = col_assy(lookupforweekadj7)
mpfadj14 = mpf_assy(lookupforweekadj14)
coladj14 = col_assy(lookupforweekadj14)
mpfadj21 = mpf_assy(lookupforweekadj21)
coladj21 = col_assy(lookupforweekadj21)

In [23]:
#mpfadj7.to_excel('T:\share\Thomas\mpfadj7.xlsx')
#coladj7.to_excel('T:\share\Thomas\coladj7.xlsx')
#mpfadj14.to_excel('T:\share\Thomas\mpfadj14.xlsx')
#coladj14.to_excel('T:\share\Thomas\coladj14.xlsx')
#mpfadj21.to_excel('T:\share\Thomas\mpfadj21.xlsx')
#coladj21.to_excel('T:\share\Thomas\coladj21.xlsx')
mpfadj7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpfadj7.xlsx')
coladj7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coladj7.xlsx')
mpfadj14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpfadj14.xlsx')
coladj14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coladj14.xlsx')
mpfadj21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpfadj21.xlsx')
coladj21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coladj21.xlsx')

In [24]:
paintadj7 = paint_schedule(mpfadj7, coladj7)
paintadj14 = paint_schedule(mpfadj14, coladj14)
paintadj21 = paint_schedule(mpfadj21, coladj21)

In [25]:
work_glass = pd.DataFrame()
work_legs = pd.DataFrame()
work_paintpack = pd.DataFrame()
work_rockwell = pd.DataFrame()
work_station50 = pd.DataFrame()
work_sysassy = pd.DataFrame()
work_tables = pd.DataFrame()
nowork_glass = pd.DataFrame()
nowork_legs = pd.DataFrame()
nowork_paintpack = pd.DataFrame()
nowork_rockwell = pd.DataFrame()
nowork_station50 = pd.DataFrame()
nowork_sysassy = pd.DataFrame()
nowork_tables = pd.DataFrame()

lookupforweekadj7x = lookupforweekadj7[['MPF','DATE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SO TYPE','SALES ORDER','WORK ORDER','SALES LINE','COLOR','AREA']]
noworkforweek7x = noworkforweek7[['MPF','DATE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SO TYPE','SALES ORDER','WORK ORDER','SALES LINE','COLOR','AREA']]

gl_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Glass']
gl_yes = gl_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
lg_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Legs']
lg_yes = lg_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
pp_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Paint/Pack']
pp_yes = pp_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
ro_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Rockwell']
ro_yes = ro_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
s5_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Station 50']
s5_yes = s5_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
sy_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Sys Assy']
sy_yes = sy_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
ta_yes = lookupforweekadj7x[lookupforweekadj7x['AREA'] == 'Tables']
ta_yes = ta_yes.sort_values(by=['DATE','OPEN PATTERN QTY'])
    
gl_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Glass']
gl_no = gl_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
lg_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Legs']
lg_no = lg_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
pp_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Paint/Pack']
pp_no = pp_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
ro_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Rockwell']
ro_no = ro_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
s5_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Station 50']
s5_no = s5_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
sy_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Sys Assy']
sy_no = sy_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
ta_no = noworkforweek7x[noworkforweek7x['AREA'] == 'Tables']
ta_no = ta_no.sort_values(by=['DATE','OPEN PATTERN QTY'])
    
for i in range(len(paintadj7)):

    appendthis1 = gl_yes[gl_yes['COLOR'] == paintadj7[i]]
    work_glass = work_glass.append(appendthis1)
    work_glass.reset_index(drop=True,inplace=True)
    appendthis2 = lg_yes[lg_yes['COLOR'] == paintadj7[i]]
    work_legs = work_legs.append(appendthis2)
    work_legs.reset_index(drop=True,inplace=True)
    appendthis3 = pp_yes[pp_yes['COLOR'] == paintadj7[i]]
    work_paintpack = work_paintpack.append(appendthis3)
    work_paintpack.reset_index(drop=True,inplace=True)
    appendthis4 = ro_yes[ro_yes['COLOR'] == paintadj7[i]]
    work_rockwell = work_rockwell.append(appendthis4)
    work_rockwell.reset_index(drop=True,inplace=True)
    appendthis5 = s5_yes[s5_yes['COLOR'] == paintadj7[i]]
    work_station50 = work_station50.append(appendthis5)
    work_station50.reset_index(drop=True,inplace=True)
    appendthis6 = sy_yes[sy_yes['COLOR'] == paintadj7[i]]
    work_sysassy = work_sysassy.append(appendthis6)
    work_sysassy.reset_index(drop=True,inplace=True)
    appendthis7 = ta_yes[ta_yes['COLOR'] == paintadj7[i]]
    work_tables = work_tables.append(appendthis7)
    work_tables.reset_index(drop=True,inplace=True)
        
    appendthis8 = gl_no[gl_no['COLOR'] == paintadj7[i]]
    nowork_glass = nowork_glass.append(appendthis8)
    nowork_glass.reset_index(drop=True,inplace=True)
    appendthis9 = lg_no[lg_no['COLOR'] == paintadj7[i]]
    nowork_legs = nowork_legs.append(appendthis9)
    nowork_legs.reset_index(drop=True,inplace=True)
    appendthis10 = pp_no[pp_no['COLOR'] == paintadj7[i]]
    nowork_paintpack = nowork_paintpack.append(appendthis10)
    nowork_paintpack.reset_index(drop=True,inplace=True)
    appendthis11 = ro_no[ro_no['COLOR'] == paintadj7[i]]
    nowork_rockwell = nowork_rockwell.append(appendthis11)
    nowork_rockwell.reset_index(drop=True,inplace=True)
    appendthis12 = s5_no[s5_no['COLOR'] == paintadj7[i]]
    nowork_station50 = nowork_station50.append(appendthis12)
    nowork_station50.reset_index(drop=True,inplace=True)
    appendthis13 = sy_no[sy_no['COLOR'] == paintadj7[i]]
    nowork_sysassy = nowork_sysassy.append(appendthis13)
    nowork_sysassy.reset_index(drop=True,inplace=True)
    appendthis14 = ta_no[ta_no['COLOR'] == paintadj7[i]]
    nowork_tables = nowork_tables.append(appendthis14)
    nowork_tables.reset_index(drop=True,inplace=True)
        
#work_glass.to_excel(r'T:\share\Thomas\work_glass.xlsx')
#work_legs.to_excel(r'T:\share\Thomas\work_legs.xlsx')
#work_paintpack.to_excel(r'T:\share\Thomas\work_paintpack.xlsx')
#work_rockwell.to_excel(r'T:\share\Thomas\work_rockwell.xlsx')
#work_station50.to_excel(r'T:\share\Thomas\work_station50.xlsx')
#work_sysassy.to_excel(r'T:\share\Thomas\work_sysassy.xlsx')
#work_tables.to_excel(r'T:\share\Thomas\work_tables.xlsx')
#nowork_glass.to_excel(r'T:\share\Thomas\nowork_glass.xlsx')
#nowork_legs.to_excel(r'T:\share\Thomas\nowork_legs.xlsx')
#nowork_paintpack.to_excel(r'T:\share\Thomas\nowork_paintpack.xlsx')
#nowork_rockwell.to_excel(r'T:\share\Thomas\nowork_rockwell.xlsx')
#nowork_station50.to_excel(r'T:\share\Thomas\nowork_station50.xlsx')
#nowork_sysassy.to_excel(r'T:\share\Thomas\nowork_sysassy.xlsx')
#nowork_tables.to_excel(r'T:\share\Thomas\nowork_tables.xlsx')

work_glass.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_glass.xlsx')
work_legs.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_legs.xlsx')
work_paintpack.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_paintpack.xlsx')
work_rockwell.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_rockwell.xlsx')
work_station50.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_station50.xlsx')
work_sysassy.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_sysassy.xlsx')
work_tables.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\work_tables.xlsx')
nowork_glass.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_glass.xlsx')
nowork_legs.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_legs.xlsx')
nowork_paintpack.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_paintpack.xlsx')
nowork_rockwell.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_rockwell.xlsx')
nowork_station50.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_station50.xlsx')
nowork_sysassy.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_sysassy.xlsx')
nowork_tables.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\nowork_tables.xlsx')

In [26]:
paintframeadj7 = pd.DataFrame(paintadj7)
paintframeadj7 = paintframeadj7[paintframeadj7[0] != 'N/A']
paintframeadj7.reset_index()
#paintframeadj7.to_excel('T:\share\Thomas\paintframeadj7.xlsx')
paintframeadj7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj7.xlsx')
paintframeadj14 = pd.DataFrame(paintadj14)
paintframeadj14 = paintframeadj14[paintframeadj14[0] != 'N/A']
paintframeadj14.reset_index()
#paintframeadj14.to_excel('T:\share\Thomas\paintframeadj14.xlsx')
paintframeadj14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj14.xlsx')
paintframeadj21 = pd.DataFrame(paintadj21)
paintframeadj21 = paintframeadj21[paintframeadj21[0] != 'N/A']
paintframeadj21.reset_index()
#paintframeadj21.to_excel('T:\share\Thomas\paintframeadj21.xlsx')
paintframeadj21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintframeadj21.xlsx')

In [27]:
lookupforweekmsadj7 = create_lookupms(allcompsadj7, paintadj7)
lookupforweekmsadj14 = create_lookupms(allcompsadj14, paintadj14)
lookupforweekmsadj21 = create_lookupms(allcompsadj21, paintadj21)

In [28]:
lookupforweekmsadj7=pd.merge(lookupforweekmsadj7,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj7 = lookupforweekmsadj7.sort_values(by=['Hours Prod'])
lookupforweekmsadj7.reset_index(drop=True,inplace=True)

lookupforweekmsadj14=pd.merge(lookupforweekmsadj14,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj14 = lookupforweekmsadj14.sort_values(by=['Hours Prod'])
lookupforweekmsadj14.reset_index(drop=True,inplace=True)

lookupforweekmsadj21=pd.merge(lookupforweekmsadj21,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekmsadj21 = lookupforweekmsadj21.sort_values(by=['Hours Prod'])
lookupforweekmsadj21.reset_index(drop=True,inplace=True)

In [29]:
compadj7 = comp_ms(lookupforweekmsadj7)
compadj14 = comp_ms(lookupforweekmsadj14)
compadj21 = comp_ms(lookupforweekmsadj21)

non_msadj7 = list(set(paintadj7) ^ set(compadj7.columns.tolist()))
paintadj7 = [e for e in paintadj7 if e not in non_msadj7]
non_msadj14 = list(set(paintadj14) ^ set(compadj14.columns.tolist()))
paintadj14 = [e for e in paintadj14 if e not in non_msadj14]
non_msadj21 = list(set(paintadj21) ^ set(compadj21.columns.tolist()))
paintadj21 = [e for e in paintadj21 if e not in non_msadj21]

In [30]:
shopadj7 = shop_schedule(paintadj7, compadj7)
shopadj14 = shop_schedule(paintadj14, compadj14)
shopadj21 = shop_schedule(paintadj21, compadj21)
#shopadj7.to_excel('T:\share\Thomas\shopadj7.xlsx')
#shopadj14.to_excel('T:\share\Thomas\shopadj14.xlsx')
#shopadj21.to_excel('T:\share\Thomas\shopadj21.xlsx')
shopadj7.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shopadj7.xlsx')
shopadj14.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shopadj14.xlsx')
shopadj21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\shopadj21.xlsx')

Truncated paintlist
E40
EL9
ET2
EKS
EKT
EZ5
EFT
EJ67
EK5
EDT
EGX
EDS


<ipython-input-16-fe785f86abcf>:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-16-fe785f86abcf>:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie['Component Totals'] = headie['Component Totals'] - number1


EK71
EG2
EJ0
EFS
ERS
EMS
E1T
EMT
E1T
Truncated paintlist
N/A
ET2
EZ5
EDT
EFT
EKT
EGX
EK5
EG2
EKS
ERS
EDS
120
E81
EMT
E81
Truncated paintlist
N/A
EZ5
ET2
EKT
E40
EKS
EJ0
EFT
ERS
EHT
146
